# Cycling Infrastructure Planning

This notebooks applies our cycling potential model (counting the cyclable trips) to the municipal planning for bicycle lanes expansion.

This way, we can describe how many trips would easily migrate to bicycle modal if its planning were implemented (thus providing evidence for its prioritization)

In [1]:
%load_ext autoreload
%autoreload 2
import saopaulo.load_trips as sptr
import saopaulo.maps_aux as aux
import saopaulo.cycling_infrastructure as cinfra
import saopaulo.choropleth as spchoro
import bikescience.map_widgets as mpw
from math import log

from shapely.geometry import LineString, Point
#import saopaulo.choropleth_folium as spchoro

import saopaulo.sp_grid as gr

from bikescience.intersect_ways import geometry_intersection_length

import geopandas as gpd
import json
import pandas as pd
import numpy as np
from ipywidgets import interact_manual, widgets, fixed
from IPython.core.display import display, HTML, clear_output
import folium

import warnings
import requests
import os
import fnmatch as fnm
warnings.simplefilter('ignore')

gr.SP_LAT = -23.63
gr.SP_LON = -46.55


/home/pedro/.local/lib/python3.8/site-packages/geopandas/_compat.py:106: UserWarning: The Shapely GEOS version (3.8.0-CAPI-1.13.1 ) is incompatible with the GEOS version PyGEOS was compiled with (3.9.0-CAPI-1.16.2). Conversions between both will be slow.
  warnings.warn(


In [2]:
districts_names = [
    'Bela Vista', 'Bom Retiro', 'Cambuci', 'Consolação', 'Liberdade', 
    'República', 'Santa Cecília', 'Sé','Butantã', 'Morumbi', 'Raposo Tavares', 
    'Rio Pequeno', 'Vila Sônia', 'Barra Funda', 'Jaguara', 'Jaguaré', 'Lapa', 
    'Perdizes', 'Vila Leopoldina', 'Alto de Pinheiros', 'Itaim Bibi', 
    'Jardim Paulista', 'Pinheiros','Aricanduva', 'Carrão', 'Vila Formosa',
    'Água Rasa', 'Belém', 'Brás', 'Mooca', 'Pari', 'Tatuapé', 'Artur Alvim',
    'Cangaíba', 'Penha', 'Vila Matilde', 'São Lucas', 'Sapopemba',
    'Vila Prudente','Cidade Tiradentes', 'Ermelino Matarazzo', 'Ponte Rasa',
    'Guaianases', 'Lajeado', 'Itaim Paulista', 'Vila Curuçá', 'Cidade Líder',
    'Itaquera', 'José Bonifácio', 'Parque do Carmo', 'Iguatemi', 'São Mateus',
    'São Rafael', 'Jardim Helena', 'São Miguel', 'Vila Jacuí','Cachoeirinha', 
    'Casa Verde', 'Limão', 'Brasilândia', 'Freguesia do Ó', 'Anhanguera', 
    'Perus', 'Jaraguá', 'Pirituba', 'São Domingos','Jaçanã', 'Tremembé', 
    'Mandaqui', 'Santana', 'Tucuruvi', 'Vila Guilherme', 'Vila Maria', 
    'Vila Medeiros','Cursino', 'Ipiranga', 'Sacomã', 'Jabaquara', 'Moema', 
    'Saúde', 'Vila Mariana', 'Campo Limpo', 'Capão Redondo', 'Vila Andrade', 
    'Cidade Dutra', 'Grajaú', 'Socorro', 'Cidade Ademar', 'Pedreira', 
    'Jardim Ângela', 'Jardim São Luís', 'Marsilac', 'Parelheiros',
    'Campo Belo', 'Campo Grande', 'Santo Amaro']

In [4]:
sao_paulo = gpd.read_file('../data/sao-paulo/SP_Municipios_2021/SP_Municipios_2021.shp')
sao_paulo = sao_paulo.loc[sao_paulo['NM_MUN'] == 'São Paulo']

In [5]:
od_trips = pd.read_csv('bases/complete_csv.csv')
# fix FE_VIA with wrong format (because of thousand separator)
od_trips.loc[od_trips['FE_VIA'] >= 10000, 'FE_VIA'] = od_trips.loc[od_trips['FE_VIA'] >= 10000, 'FE_VIA'] / 1000
od_trips.dropna(inplace = True)
od_trips = gpd.GeoDataFrame(od_trips, crs={'init': 'epsg:4326'},
                 geometry=[LineString(eval(r)) for r in od_trips['route']])
od_trips['final_potential_v2'] = (od_trips['distance_potential'] + od_trips['inclination_potential'])/2

In [6]:
protected_lanes = cinfra.load_protected_lanes('../data/sao-paulo/infraestrutura-cicloviaria/cet/Ciclovias.shp')
bike_lanes = cinfra.load_bike_lanes('../data/sao-paulo/infraestrutura-cicloviaria/cet/Ciclovias.shp')
infra = pd.concat([protected_lanes, bike_lanes])

In [7]:
planned_lanes = gpd.read_file('../data/sao-paulo/infraestrutura-cicloviaria/shapesInfraestruturaCicloviaria/CicloviasConexoes.shp')
planned_lanes.crs = {'init': 'epsg:4326'}  
#planned_lanes.to_crs(epsg='4326', inplace=True)

fmap = gr.map_around_sp(the_grid=None,zoom=10,plot_grid=False)
folium.GeoJson(planned_lanes, style_function = lambda x : {'color': 'black', 'weight': 2, 'opacity': 1, 'fillColor': 'black'},
                   name='ruas', control=False).add_to(fmap)

display(fmap)

In [15]:
colors = ['#ffffb2','#fed976','#feb24c','#fd8d3c','#f03b20', '#bd0026'] #YlOrRd
colors = ['#a1d99b','#74c476','#41ab5d','#238b45','#006d2c','#00441b'] #green
colors = ['#ED553B','#F6D55C','#3CAEA3','#20639B'] #multi color
colors = ['#E1F5FE','#B3E5FC','#81D4FA','#4FC3F7','#29B6F6','#03A9F4','#039BE5','#0288D1','#0277BD','#01579B'] #blue
colors = ['#FEF001','#FFCE03','#FD9A01','#FD6104','#FF2C05','#F00505'] #Yellow to Red

n = len(colors)
intervals     = [i/n for i in range(1, n + 1)]                # [0.20, 0.40, 0.60, 0.80, 1]
intervals_sq  = [(i/n)**2 for i in range(1, n + 1)]           # [0.04, 0.16, 0.36, 0.64, 1] detalha valores baixos
intervals_log = [log(i + 1, n + 1) for i in range(1, n + 1)]  # [0.38, 0.61, 0.77, 0.89, 1] detalha valores altos

intervals = intervals_sq

round_factor = 100

def get_color (potential, min_trip, max_trip):
    for i in range(n):
        if potential <= min_trip + intervals[i] * (max_trip - min_trip): return colors[i];

def build_subtitle (min_trip, max_trip):
    subtitle = []
    for i in range(n):
        subtitle.append([colors[i], round((min_trip + intervals[i] * (max_trip - min_trip)) / round_factor) * round_factor])
    subtitle.reverse()
    return subtitle

In [10]:
import datetime
def trips_per_lane(trips, lanes, expansion = 'FE_VIA'):
    expansions = trips[expansion]
    trips_lane = [0]*len(lanes)
    progress = 0
    for l in range(len(lanes)):
        
        if l / len(lanes) >= progress:
            print (round(progress * 100), '%  - ', datetime.datetime.now().strftime("%Y-%m-%d %H:%M:%S"))
            progress += 0.2
        
        lane = lanes.iloc[l]['geometry']
        for t in range(len(trips)):
            trip = trips.iloc[t]['geometry']
            if (lane.distance(trip) < 0.0005):
                trips_lane[l] += expansions.iloc[t]
    return trips_lane  

In [17]:
def add_infra_layer(fmap):
    style_infra = lambda style:{'color':'blue', 'weight': 2 }
    folium.GeoJson(infra, show = False, control = True,
        style_function = style_infra,
        name = 'bike lanes').add_to(fmap)
    folium.LayerControl().add_to(fmap)

def plot_potential_lanes(lanes, title = "", display_map = True, show_greater_than = .05, plot_infra = True, 
                         column = None):
        
    fmap = gr.map_around_sp(the_grid=None,zoom=10, plot_grid=False)
            
    max_trip = max(lanes[column])
    lanes_aux = lanes.loc[lanes[column] > show_greater_than*max_trip ]
    min_trip = min(lanes_aux[column])
    
    #spchoro.plot_zones_border(fmap, zone_shp, '#333333', plot_rmsp = False, weight = 0.7)
    
    style_sao_paulo = lambda style:{'color':'black', 'weight': 1.5, 'fill': False }
    folium.GeoJson(sao_paulo, style_sao_paulo, control = False).add_to(fmap)
    
    style_lanes = lambda x : {'color':get_color(x['properties'][column], min_trip, max_trip), 
                              'weight': 1 + (5 * x['properties'][column] / max_trip), 'opacity': 0.95}
    folium.GeoJson(lanes_aux, style_lanes, control=False).add_to(fmap)
    
    if (plot_infra):
        add_infra_layer(fmap)
    
    fmap.get_root().html.add_child(folium.Element(mpw.build_title('Cyclable Trips')))    
    fmap.get_root().html.add_child(folium.Element(mpw.build_legend_lines('Trips', build_subtitle(min_trip, max_trip))))
    fmap.get_root().html.add_child(folium.Element(mpw.drag_function('Trips')))
    
    fmap.save('maps/cycling_infrastructure_planning/' + title + '.html')
    if (display_map):
        display(fmap)

In [11]:
#trips = od_trips.loc[(((od_trips['ZONA_O'] >= 339) & (od_trips['ZONA_O'] <= 442)) | 
#                      ((od_trips['ZONA_D'] >= 339) & (od_trips['ZONA_D'] <= 442))) & 
#                     (od_trips['final_potential'] > .8)]

trips = od_trips.loc[od_trips['final_potential_v2'] > .75]

planned_lanes['potential_trips'] = trips_per_lane(trips, planned_lanes)

0 %  -  2023-03-08 12:45:29
20 %  -  2023-03-08 12:50:29
40 %  -  2023-03-08 12:55:09
60 %  -  2023-03-08 12:59:47
80 %  -  2023-03-08 13:04:20


In [12]:
display(planned_lanes.sort_values('potential_trips', ascending = False)[['nome','logradouro', 'potential_trips']].head(30))

nome  \
112                             RADIAL LESTE   
111                             RADIAL LESTE   
22                    ARMANDO ARRUDA PEREIRA   
23                                   BRESSER   
59                              INDIANOPOLIS   
72                          JOAO TEODORO - I   
103                          PEDRO DE TOLEDO   
96                         PE ARLINDO VIEIRA   
76              LUIZ IGNACIO ANHAIA MELO - I   
110                             RADIAL LESTE   
128  RUI BARBOSA-TREZE DE MAIO-SANTO ANTONIO   
39                                    DARZAN   
21                    ARMANDO ARRUDA PEREIRA   
137                 TIRADENTES-SANTOS DUMONT   
102                          PEDRO DE TOLEDO   
105                                  POMPEIA   
34                          CARLOS DE CAMPOS   
124                          RIBEIRO DE LIMA   
142                VICENTE RAO-ROQUE PETRONE   
153                            AGUIA DE HAIA   
35                                   CURSINO   
77              LUIZ IGNACIO ANHAIA MELO - I   
104                                    PIAUI   
67                JOAO PAULO I-MIGUEL CONEJO   
123                          RIBEIRO DE LIMA   
131  RUI BARBOSA-TREZE DE MAIO-SANTO ANTONIO   
129  RUI BARBOSA-TREZE DE MAIO-SANTO ANTONIO   
4                   TIRADENTES-SANTOS DUMONT   
29                      CAP PACHECO E CHAVES   
11                            ABRAAO RIBEIRO   

                             logradouro  potential_trips  
112              AV   ALCANTARA MACHADO     60503.844523  
111                     R   MELO FREIRE     55329.747920  
22    AV ENG  ARMANDO DE ARRUDA PEREIRA     35791.717954  
23                         VD   BRESSER     30586.614967  
59                    AV   INDIANOPOLIS     28540.049496  
72                       R JOAO TEODORO     26440.255183  
103                 R   PEDRO DE TOLEDO     25463.333779  
96               AV PDE  ARLINDO VIEIRA     20767.302182  
76   AV PROF  LUIZ IGNACIO ANHAIA MELLO     20563.937723  
110              VD   ALCANTARA MACHADO     19272.038927  
128                 R   JOAO PASSALAQUA     19107.130421  
39                         AV BRAZ LEME     18954.603296  
21    AV ENG  ARMANDO DE ARRUDA PEREIRA     18705.749906  
137                       AV TIRADENTES     17510.860752  
102                 R   PEDRO DE TOLEDO     17064.087775  
105                        AV   POMPEIA     16954.541076  
34                AV   CARLOS DE CAMPOS     16924.877185  
124                 R   RIBEIRO DE LIMA     16919.439781  
142           AV   ROQUE PETRONI JUNIOR     16799.029681  
153                  AV   AGUIA DE HAIA     16141.235801  
35                       AV  DO CURSINO     16094.280978  
77   AV PROF  LUIZ IGNACIO ANHAIA MELLO     16021.563438  
104                           R   PIAUI     15237.845857  
67                    AV   JOAO PAULO I     14825.382234  
123                 R   RIBEIRO DE LIMA     14552.752496  
131                   R   TREZE DE MAIO     14500.452150  
129                     R   RUI BARBOSA     14480.432180  
4                    AV   SANTOS DUMONT     13893.188587  
29                      R   COELHO NETO     13402.471462  
11                AV DR  ABRAAO RIBEIRO     13093.789539

In [18]:
plot_potential_lanes(planned_lanes, 'all_cyclable_trips', column='potential_trips')

In [19]:
motorized_trips = od_trips.loc[od_trips['final_potential'] > .75].loc[
    (od_trips['modal'] == 'car') | 
    (od_trips['modal'] == 'motorcycle')]

planned_lanes['potential_trips_car'] = trips_per_lane(motorized_trips, planned_lanes)

0 %  -  2023-03-08 13:46:23
20 %  -  2023-03-08 13:47:16
40 %  -  2023-03-08 13:48:08
60 %  -  2023-03-08 13:49:05
80 %  -  2023-03-08 13:49:50


In [20]:
display(planned_lanes.sort_values('potential_trips_car', ascending = False)[['nome','logradouro', 'potential_trips', 'potential_trips_car']].head(30))

nome  \
96                         PE ARLINDO VIEIRA   
59                              INDIANOPOLIS   
143                VICENTE RAO-ROQUE PETRONE   
142                VICENTE RAO-ROQUE PETRONE   
18                                  ARAGUARI   
103                          PEDRO DE TOLEDO   
22                    ARMANDO ARRUDA PEREIRA   
132                                S QUIRINO   
19                           ARATAS-ANAPURUS   
102                          PEDRO DE TOLEDO   
105                                  POMPEIA   
76              LUIZ IGNACIO ANHAIA MELO - I   
67                JOAO PAULO I-MIGUEL CONEJO   
112                             RADIAL LESTE   
38                                 D PEDRO I   
129  RUI BARBOSA-TREZE DE MAIO-SANTO ANTONIO   
39                                    DARZAN   
153                            AGUIA DE HAIA   
128  RUI BARBOSA-TREZE DE MAIO-SANTO ANTONIO   
106                      PRES TANCREDO NEVES   
31                           CARLOS CALDEIRA   
98           PEDRA AZUL-SANGIRARDI-D AVELINA   
34                          CARLOS DE CAMPOS   
80                               MARIA MALUF   
37                                 D PEDRO I   
44                   EDGAR FACO-MQ S VICENTE   
17                                 ANASTACIO   
47                   EDGAR FACO-MQ S VICENTE   
45                   EDGAR FACO-MQ S VICENTE   
43                   EDGAR FACO-MQ S VICENTE   

                             logradouro  potential_trips  potential_trips_car  
96               AV PDE  ARLINDO VIEIRA     20767.302182          5002.487593  
59                    AV   INDIANOPOLIS     28540.049496          4590.431795  
143                AV VER  JOAO DE LUCA      8251.290934          4381.964077  
142           AV   ROQUE PETRONI JUNIOR     16799.029681          3698.338756  
18                         R   ARAGUARI      7553.244965          3353.875972  
103                 R   PEDRO DE TOLEDO     25463.333779          3135.963325  
22    AV ENG  ARMANDO DE ARRUDA PEREIRA     35791.717954          3103.168596  
132                        R S  QUIRINO      5344.382692          3004.535970  
19                          AV   ARATAS      6603.796220          2368.116025  
102                 R   PEDRO DE TOLEDO     17064.087775          2253.702594  
105                        AV   POMPEIA     16954.541076          2108.792895  
76   AV PROF  LUIZ IGNACIO ANHAIA MELLO     20563.937723          2072.348629  
67                    AV   JOAO PAULO I     14825.382234          2033.744537  
112              AV   ALCANTARA MACHADO     60503.844523          1968.869528  
38                      AV DOM  PEDRO I      7049.618214          1901.740270  
129                     R   RUI BARBOSA     14480.432180          1873.954789  
39                         AV BRAZ LEME     18954.603296          1842.817492  
153                  AV   AGUIA DE HAIA     16141.235801          1822.674161  
128                 R   JOAO PASSALAQUA     19107.130421          1719.850660  
106             AV PRES  TANCREDO NEVES     12391.667423          1685.933082  
31           AV   CARLOS CALDEIRA FILHO      6121.382463          1658.622785  
98                       R   PEDRA AZUL      7236.803969          1606.950508  
34                AV   CARLOS DE CAMPOS     16924.877185          1516.396757  
80                    TUN   MARIA MALUF      8424.148902          1450.015203  
37                      AV DOM  PEDRO I      3110.833394          1418.938911  
44                AV   ERMANO MARCHETTI      8404.162505          1350.947866  
17                     AV  DO ANASTACIO      2131.092820          1314.465246  
47                   AV GAL  EDGAR FACO      2297.816232          1300.168838  
45                        PTE   PIQUERI      6710.810006          1300.168838  
43                        PTE   PIQUERI      6988.367043          1300.168838

In [22]:
plot_potential_lanes(planned_lanes, 'motorized_trips', column='potential_trips_car')

In [23]:
trips = od_trips.loc[od_trips['final_potential_v2'] > .75].loc[od_trips['modal'] == 'pedestrian']

planned_lanes['potential_trips_pedestrian'] = trips_per_lane(trips, planned_lanes)

0 %  -  2023-03-08 13:51:24
20 %  -  2023-03-08 13:53:51
40 %  -  2023-03-08 13:56:31
60 %  -  2023-03-08 13:59:24
80 %  -  2023-03-08 14:01:52


In [24]:
display(planned_lanes.sort_values('potential_trips_pedestrian', ascending = False)[['nome', 'potential_trips_pedestrian']].head(10))

nome  potential_trips_pedestrian
22                    ARMANDO ARRUDA PEREIRA                16357.383124
112                             RADIAL LESTE                11976.907375
96                         PE ARLINDO VIEIRA                11720.396456
21                    ARMANDO ARRUDA PEREIRA                11006.067858
153                            AGUIA DE HAIA                10314.365156
128  RUI BARBOSA-TREZE DE MAIO-SANTO ANTONIO                 9520.523161
142                VICENTE RAO-ROQUE PETRONE                 8806.914799
105                                  POMPEIA                 8686.774265
131  RUI BARBOSA-TREZE DE MAIO-SANTO ANTONIO                 8135.958245
72                          JOAO TEODORO - I                 7577.852047

In [25]:
plot_potential_lanes(planned_lanes, 'pedestrian_trips', column='potential_trips_pedestrian')